In [8]:
import cadquery as cq
from cadquery import Workplane, Assembly, Location, Vector, Color, exporters
# from cq_server.ui import ui, show_object
# from ocp_vscode import *

from ocp_vscode import show, show_object, reset_show, set_port, set_defaults, get_defaults
set_port(3939)

In [9]:
reset_show()

In [10]:
# Define a unit for micrometers.
um = 0.001

def build_cell(pad_length, di_thickness):
    """
    Build a single capacitor cell.
    
    Parameters:
      pad_length (float): The pad length (formerly c_pad_width) in µm.
      di_thickness (float): The dielectric thickness (formerly via_thickness) in µm.
      
    Returns:
      dict: Dictionary containing the six parts as CadQuery solids.
            Keys: "bot_CI", "signal_CI", "via", "top_electrode", "top_connector", "DI".
    """
    # Basic parameters (all dimensions in µm, then scaled by um)
    bar_width      = 300 * um
    bar_length     = 2000 * um
    bar_thickness  = 20 * um
    gap            = 2000 * um

    top_bar_width  = 2300 * um
    top_bar_length = 300 * um

    c_bridge_width = 300 * um
    c_bridge_length= 450 * um

    signal_pad_length = 550 * um

    via_r = c_bridge_width / 2

    # Build the bottom layer (bot_CI)
    wp = cq.Workplane("XY")
    left_bar = wp.rect(bar_width, bar_length, centered=False).extrude(bar_thickness)
    right_bar = cq.Workplane("XY").move(gap, 0).rect(bar_width, bar_length, centered=False).extrude(bar_thickness)
    top_bar = cq.Workplane("XY").moveTo(0, 0).move(0, bar_length)\
                .rect(top_bar_width, top_bar_length, centered=False).extrude(bar_thickness)
    c_bridge = cq.Workplane("XY").move(gap/2, bar_length)\
                 .rect(c_bridge_width, -c_bridge_length, centered=False).extrude(bar_thickness)
    c_pad = cq.Workplane("XY").moveTo(top_bar_width/2, (bar_length - c_bridge_length) - (pad_length)/2)\
                 .rect(pad_length, pad_length, centered=True).extrude(bar_thickness)
    bot_CI = left_bar.union(right_bar).union(top_bar).union(c_bridge).union(c_pad)
    
    # Build the signal pad.
    signal_CI = cq.Workplane("XY").move(gap/2, 0)\
                     .rect(bar_width, signal_pad_length, centered=False).extrude(bar_thickness)
    
    
    # Build the via.
    via = cq.Workplane("XY").moveTo(top_bar_width/2, signal_pad_length)\
              .circle(via_r).extrude(di_thickness + 2*bar_thickness)
    
    
    # Build the top electrode.
    top_electrode = cq.Workplane("XY").workplane(offset=di_thickness + bar_thickness)\
                        .moveTo(top_bar_width/2, (bar_length - c_bridge_length) - (pad_length)/2)\
                        .rect(pad_length, pad_length, centered=True).extrude(bar_thickness)
    
    
    # Build the top connector.
    top_connector = cq.Workplane("XY").workplane(offset=di_thickness + bar_thickness)\
                        .moveTo(top_bar_width/2 - c_bridge_width/2, (bar_length - c_bridge_length - pad_length))\
                        .rect(c_bridge_width, -(bar_length - c_bridge_length - pad_length - signal_pad_length), centered=False)\
                        .extrude(bar_thickness)
    top_ci = top_electrode.union(top_connector)
    
    # Build the DI (dielectric island) layer.
    # Its reference point is defined relative to the top-left corner of the pad.
    c_pad_tl = (
        c_pad.faces(">Z")
        .vertices("<X and >Y")
        .val()
        .Center()
    )
    DI = cq.Workplane("XY").moveTo(c_pad_tl.x - 100*um, c_pad_tl.y + 100*um)\
             .rect(pad_length + 200*um, -(bar_length - c_bridge_length - bar_width), centered=False)\
             .extrude(di_thickness+bar_thickness)
    
    
    return {
        "bot_CI": bot_CI,
        "signal_CI": signal_CI,
        "via": via,
        "top_ci": top_ci,
        "DI": DI
    }

In [11]:
def make_cal_open(pad_length,DI_thickness):
    """Create a calibration open structure for the design."""

    # Basic parameters (all dimensions in µm, then scaled by um)
    bar_width      = 300 * um
    bar_length     = 2000 * um
    bar_thickness  = 20 * um
    gap            = 2000 * um

    top_bar_width  = 2300 * um
    top_bar_length = 300 * um

    c_bridge_width = 300 * um
    c_bridge_length= 450 * um

    signal_pad_length = 550 * um

    via_r = c_bridge_width / 2

    # The Bot CI Pad
    wp = Workplane("XY")
    left_bar = (wp.rect(bar_width, bar_length,centered=False).extrude(bar_thickness))
    right_bar = (wp.move(gap, 0).rect(bar_width, bar_length,centered=False).extrude(bar_thickness))
    top_bar = (wp.moveTo(0,0).move(0,bar_length).rect(top_bar_width,top_bar_length,centered=False).extrude(bar_thickness))
    c_bridge = (wp.move(gap/2,bar_length).rect(c_bridge_width,-c_bridge_length,centered=False)
        .extrude(bar_thickness))
    c_pad = (wp.moveTo((top_bar_width/2),(bar_length - c_bridge_length)-pad_length/2).rect(pad_length,pad_length,centered=True)
        .extrude(bar_thickness))
    
    bot_ci = left_bar.union(right_bar).union(top_bar).union(c_bridge).union(c_pad)

    # The Signal Pad
    signal_pad = (
        wp.move(gap/2,0)
        .rect(bar_width,signal_pad_length,centered=False)
        .extrude(bar_thickness)
    )
    # The Top CI
    """ top_electrode = (
        wp.workplane(offset=DI_thickness+bar_thickness)
        .moveTo((top_bar_width/2),(bar_length - c_bridge_length)-pad_length/2)
        .rect(pad_length, pad_length, centered=True)
        .extrude(bar_thickness)
    ) """

    top_connector = (
        wp.workplane(offset=DI_thickness+bar_thickness)
        .moveTo((top_bar_width/2 -c_bridge_width/2 ),(bar_length - c_bridge_length - pad_length))
        .rect(c_bridge_width,-(bar_length-c_bridge_length-pad_length-signal_pad_length),centered=False)
        .extrude(bar_thickness)
    )
    top_ci = top_connector
    
    # The Via
    via = (
        wp.moveTo((top_bar_width/2),signal_pad_length)
        .circle(via_r)
        .extrude(DI_thickness+2*bar_thickness)
    )

    # The DI Layer
    c_pad_tl = (
        c_pad.faces(">Z")
        .vertices("<X and >Y")
        .val()
        .Center()
    )
    DI = (
        wp.moveTo(c_pad_tl.x - 100*um, c_pad_tl.y + 100*um)
        .rect(pad_length+200*um,-(bar_length - c_bridge_length - bar_width),centered=False)
        .extrude(DI_thickness+bar_thickness)
    )

    return(
        {
            "bot_CI": bot_ci,
            "signal_CI": signal_pad,
            "via": via,
            "top_ci": top_ci,
            "DI": DI
        }
    )



In [12]:
def make_cal_short(pad_length, DI_thickness):
    """Create a calibration short structure for the design."""
    # Basic parameters (all dimensions in µm, then scaled by um)
    bar_width      = 300 * um
    bar_length     = 2000 * um
    bar_thickness  = 20 * um
    gap            = 2000 * um

    top_bar_width  = 2300 * um
    top_bar_length = 300 * um

    c_bridge_width = 300 * um
    c_bridge_length= 450 * um

    signal_pad_length = 550 * um

    via_r = c_bridge_width / 2

    wp = Workplane("XY")
    left_bar = (
        wp.rect(bar_width, bar_length,centered=False)
        .extrude(bar_thickness)
    )
    right_bar = (
        wp.move(gap, 0)
        .rect(bar_width, bar_length,centered=False)
        .extrude(bar_thickness)
    )
    top_bar = (
        wp.moveTo(0,0)
        .move(0,bar_length)
        .rect(top_bar_width,top_bar_length,centered=False)
        .extrude(bar_thickness)
    )
    c_bridge = (
        wp.move(gap/2,bar_length)
        .rect(c_bridge_width,-c_bridge_length,centered=False)
        .extrude(bar_thickness)
    )
    c_pad = (
        wp.moveTo((top_bar_width/2),(bar_length - c_bridge_length)-pad_length/2)
        .rect(pad_length,pad_length,centered=True)
        .extrude(bar_thickness)
    )

    bot_ci = left_bar.union(right_bar).union(top_bar).union(c_bridge).union(c_pad)

    # The Signal Pad
    signal_pad = (
        wp.move(gap/2,0)
        .rect(bar_width,signal_pad_length,centered=False)
        .extrude(bar_thickness)
    )
    # The Top CI
    top_electrode = (
        wp.workplane(offset=DI_thickness+bar_thickness)
        .moveTo((top_bar_width/2),(bar_length - c_bridge_length)-pad_length/2)
        .rect(pad_length, pad_length, centered=True)
        .extrude(bar_thickness)
    )

    top_connector = (
        wp.workplane(offset=DI_thickness+bar_thickness)
        .moveTo((top_bar_width/2 -c_bridge_width/2 ),(bar_length - c_bridge_length - pad_length))
        .rect(c_bridge_width,-(bar_length-c_bridge_length-pad_length-signal_pad_length),centered=False)
        .extrude(bar_thickness)
    )
    top_CI = top_electrode.union(top_connector)
    
    # The Via
    via = (
        wp.moveTo((top_bar_width/2),signal_pad_length)
        .circle(via_r)
        .extrude(DI_thickness+2*bar_thickness)
    )
    # Shorted Via
    # Find the center of the top face of c_pad
    c_pad_top_face_center = (
        c_pad.faces(">Z")  # Select the top face of c_pad
        .workplane(centerOption="CenterOfMass")  # Create a workplane at the center of mass
        .val()  # Get the face
        .Center()  # Get the center of the face as a vector
    )

    # Create an independent s_via at the center of the c_pad's top face
    s_via = (
        Workplane("XY")  # Start a new workplane
        .moveTo(c_pad_top_face_center.x, c_pad_top_face_center.y)  # Move to the center of the top face
        .circle(100 * um)  # Create a circle with radius 100 um
        .extrude(DI_thickness + bar_thickness)  # Extrude with the specified thickness
    )

    # The DI Layer
    c_pad_tl = (
        c_pad.faces(">Z")
        .vertices("<X and >Y")
        .val()
        .Center()
    )
    DI = (
        wp.moveTo(c_pad_tl.x - 100*um, c_pad_tl.y + 100*um)
        .rect(pad_length+200*um,-(bar_length - c_bridge_length - bar_width),centered=False)
        .extrude(DI_thickness+bar_thickness)
    )

    return(
        {
            "bot_CI": bot_ci,
            "signal_CI": signal_pad,
            "via": via,
            "top_ci": top_CI,
            "DI": DI,
            "s_via": s_via
        }
        
    )


In [17]:
def make_align_marker(bar_length, bar_width, thickness):
    bar_length *= um
    bar_width *= um
    thickness *= um
    wp = cq.Workplane("XY")
    # Horizontal bar
    bar1 = (wp.rect(bar_length, bar_width, centered=True).extrude(thickness))
    # Vertical bar
    bar2 = (wp.rect(bar_width, bar_length, centered=True).extrude(thickness))
    align_marker = bar1.union(bar2)
    return align_marker


In [21]:

def build_array():
    """
    Build a 10x10 array of capacitor cells and organize each layer into its own assembly.
    
    - Rows: vary pad_length from 200 to 650 µm (row 0: 200, row 1: 250, …, row 9: 650)
    - Columns: vary di_thickness among: 20, 30, 40, 50, 60, 80, 100, 120, 160, 200 µm.
    
    Returns:
      Tuple containing:
        - Global assemblies for each layer (bot_CI, signal_CI, via, top_electrode, top_connector, DI)
        - A combined final assembly (which includes all layers)
    """
    # Parameter lists.
    um = 0.001  # micrometers
    pad_lengths = [x * um for x in [200, 250, 300, 350, 400, 450, 500, 550, 600, 650, 700]]
    di_thicknesses = [x * um for x in [20, 30, 40, 50, 60, 80, 100, 120, 160, 200]]
    # Set spacing so cells do not overlap.
    spacing_x = 3000 * um
    spacing_y = 3000 * um

    # Global assemblies for each layer.
    assy_bot_CI       = cq.Assembly()
    assy_signal_CI    = cq.Assembly()
    assy_via          = cq.Assembly()
    assy_top_ci       = cq.Assembly()
    assy_DI           = cq.Assembly()
    assy_s_via        = cq.Assembly() # This is only for the shorted via
    assy_text         = cq.Assembly()  # This is for the cross align marker and text
    
    for row in range(11):
        for col in range(10):
            cell_parts = build_cell(pad_lengths[row], di_thicknesses[col])
            # Calculate the cell's placement offset.
            x_offset = col * spacing_x
            y_offset = row * spacing_y
            loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
            # Add each part to its corresponding global assembly.
            assy_bot_CI.add(cell_parts["bot_CI"], name=f"bot_CI_{row}_{col}", loc=loc,color=Color("gray"))
            assy_signal_CI.add(cell_parts["signal_CI"], name=f"signal_CI_{row}_{col}", loc=loc,color=Color("gray"))
            assy_via.add(cell_parts["via"], name=f"via_{row}_{col}", loc=loc,color=Color("gray"))
            assy_top_ci.add(cell_parts["top_ci"], name=f"top_ci_{row}_{col}", loc=loc,color=Color("gray"))
            assy_DI.add(cell_parts["DI"], name=f"DI_{row}_{col}", loc=loc,color=Color("Quantity_NOC_DARKGOLDENROD2"))

    # Add calibration on Row # 12 and 13
    # Row # 12 - The Open Structures
    row = 11
    for col in range(10):
        cell_parts = make_cal_open(pad_lengths[5], di_thicknesses[col])
        # Calculate the cell's placement offset.
        x_offset = col * spacing_x
        y_offset = 11 * spacing_y
        loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
        # Add each part to its corresponding global assembly.
        assy_bot_CI.add(cell_parts["bot_CI"], name=f"bot_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_bot_CI.add(cell_parts["signal_CI"], name=f"signal_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_via.add(cell_parts["via"], name=f"via_{row}_{col}", loc=loc,color=Color("gray"))
        assy_top_ci.add(cell_parts["top_ci"], name=f"top_ci_{row}_{col}", loc=loc,color=Color("gray"))
        assy_DI.add(cell_parts["DI"], name=f"DI_{row}_{col}", loc=loc,color=Color("Quantity_NOC_DARKGOLDENROD2"))

    # Row # 13 - The Short Structures
    row  = 12 
    for col in range (10):
        cell_parts = make_cal_short(pad_lengths[5], di_thicknesses[col])
        # Calculate the cell's placement offset.
        x_offset = col * spacing_x
        y_offset = 12 * spacing_y
        loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
        # Add each part to its corresponding global assembly.
        assy_bot_CI.add(cell_parts["bot_CI"], name=f"bot_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_signal_CI.add(cell_parts["signal_CI"], name=f"signal_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_via.add(cell_parts["via"], name=f"via_{row}_{col}", loc=loc,color=Color("gray"))
        assy_top_ci.add(cell_parts["top_ci"], name=f"top_ci_{row}_{col}", loc=loc,color=Color("gray"))
        assy_DI.add(cell_parts["DI"], name=f"DI_{row}_{col}", loc=loc,color=Color("Quantity_NOC_DARKGOLDENROD2"))
        assy_s_via.add(cell_parts["s_via"], name=f"s_via_{row}_{col}", loc=loc,color=Color("gray"))  # Add the shorted via layer
    # Add Cross Align Marker
    marker = make_align_marker(1000,200,20)
    x_offset = 10.5 * spacing_x
    y_offset = 12.5 * spacing_y
    loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
    assy_text.add(marker,name = "AlignMarker", loc = loc, color=Color("gray"))
    # Combine all layers into one final assembly.
    final_assy = cq.Assembly()
    final_assy.add(assy_bot_CI, name="bot_CI_layer")
    final_assy.add(assy_signal_CI, name="signal_CI_layer")
    final_assy.add(assy_via, name="via_layer")
    final_assy.add(assy_top_ci, name="top_electrode_layer")
    final_assy.add(assy_DI, name="DI_layer")
    final_assy.add(assy_s_via, name="s_via_layer")  # Add the shorted via layer if needed
    final_assy.add(assy_text, name="align_marker")
    
    return (assy_bot_CI, assy_signal_CI, assy_via, assy_top_ci, assy_DI, assy_s_via,assy_text, final_assy)

# Runcode
reset_show()
# Build the assemblies.
assy_bot_CI, assy_signal_CI, assy_via, assy_top_ci, assy_DI, assy_s_via,assy_text, final_assy = build_array()

# Display the final combined assembly.
show_object(final_assy, name="FinalAssembly")
# Export each individual layer to a STEP file.



ccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccc


In [22]:
import os

# Define the output folder.
output_folder = "c1-output"
os.makedirs(output_folder, exist_ok=True)

# Export each individual layer to a STEP file in the output folder.
assy_bot_CI.save(os.path.join(output_folder, "bot_CI_layer.step"))
assy_signal_CI.save(os.path.join(output_folder, "signal_CI_layer.step"))
assy_via.save(os.path.join(output_folder, "via_layer.step"))
assy_top_ci.save("C1-output\top_ci.step")
assy_DI.save(os.path.join(output_folder, "DI_layer.step"))
assy_s_via.save(os.path.join(output_folder, "s_via_layer.step"))  # Export the shorted via layer
assy_text.save(os.path.join(output_folder, "text.step"))  # Export the align marker

# Export the combined final assembly.
final_assy.save(os.path.join(output_folder, "GSG1000-W-Calibration.step"))

/Users/ryan/Project/Python-Cad/.conda/lib/python3.11/site-packages/cadquery/utils.py:39: FutureWarning: save will be removed in the next release.
  warn(f"{f.__name__} will be removed in the next release.", FutureWarning)


# The Test Print

In [26]:

def build_array_test():
    """
    Build a 10x10 array of capacitor cells and organize each layer into its own assembly.
    
    - Rows: vary pad_length from 200 to 650 µm (row 0: 200, row 1: 250, …, row 9: 650)
    - Columns: vary di_thickness among: 20, 30, 40, 50, 60, 80, 100, 120, 160, 200 µm.
    
    Returns:
      Tuple containing:
        - Global assemblies for each layer (bot_CI, signal_CI, via, top_electrode, top_connector, DI)
        - A combined final assembly (which includes all layers)
    """
    # Parameter lists.
    um = 0.001  # micrometers
    pad_lengths = [x * um for x in [200,450,700]]
    di_thicknesses = [x * um for x in [20, 80, 200]]
    # Set spacing so cells do not overlap.
    spacing_x = 3000 * um
    spacing_y = 3000 * um

    # Global assemblies for each layer.
    assy_bot_CI       = cq.Assembly()
    assy_signal_CI    = cq.Assembly()
    assy_via          = cq.Assembly()
    assy_top_ci       = cq.Assembly()
    assy_DI           = cq.Assembly()
    assy_s_via        = cq.Assembly() # This is only for the shorted via
    assy_text         = cq.Assembly()  # This is for the cross align marker and text
    
    for row in range(3):
        for col in range(3):
            cell_parts = build_cell(pad_lengths[row], di_thicknesses[col])
            # Calculate the cell's placement offset.
            x_offset = col * spacing_x
            y_offset = row * spacing_y
            loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
            # Add each part to its corresponding global assembly.
            assy_bot_CI.add(cell_parts["bot_CI"], name=f"bot_CI_{row}_{col}", loc=loc,color=Color("gray"))
            assy_signal_CI.add(cell_parts["signal_CI"], name=f"signal_CI_{row}_{col}", loc=loc,color=Color("gray"))
            assy_via.add(cell_parts["via"], name=f"via_{row}_{col}", loc=loc,color=Color("gray"))
            assy_top_ci.add(cell_parts["top_ci"], name=f"top_ci_{row}_{col}", loc=loc,color=Color("gray"))
            assy_DI.add(cell_parts["DI"], name=f"DI_{row}_{col}", loc=loc,color=Color("Quantity_NOC_DARKGOLDENROD2"))

    # Add calibration on Row # 12 and 13
    # Row # 12 - The Open Structures
    row = 3
    for col in range(3):
        cell_parts = make_cal_open(pad_lengths[1], di_thicknesses[col])
        # Calculate the cell's placement offset.
        x_offset = col * spacing_x
        y_offset = 3 * spacing_y
        loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
        # Add each part to its corresponding global assembly.
        assy_bot_CI.add(cell_parts["bot_CI"], name=f"bot_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_bot_CI.add(cell_parts["signal_CI"], name=f"signal_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_via.add(cell_parts["via"], name=f"via_{row}_{col}", loc=loc,color=Color("gray"))
        assy_top_ci.add(cell_parts["top_ci"], name=f"top_ci_{row}_{col}", loc=loc,color=Color("gray"))
        assy_DI.add(cell_parts["DI"], name=f"DI_{row}_{col}", loc=loc,color=Color("Quantity_NOC_DARKGOLDENROD2"))

    # Row # 13 - The Short Structures
    row  = 4 
    for col in range (3):
        cell_parts = make_cal_short(pad_lengths[1], di_thicknesses[col])
        # Calculate the cell's placement offset.
        x_offset = col * spacing_x
        y_offset = 4 * spacing_y
        loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
        # Add each part to its corresponding global assembly.
        assy_bot_CI.add(cell_parts["bot_CI"], name=f"bot_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_signal_CI.add(cell_parts["signal_CI"], name=f"signal_CI_{row}_{col}", loc=loc,color=Color("gray"))
        assy_via.add(cell_parts["via"], name=f"via_{row}_{col}", loc=loc,color=Color("gray"))
        assy_top_ci.add(cell_parts["top_ci"], name=f"top_ci_{row}_{col}", loc=loc,color=Color("gray"))
        assy_DI.add(cell_parts["DI"], name=f"DI_{row}_{col}", loc=loc,color=Color("Quantity_NOC_DARKGOLDENROD2"))
        assy_s_via.add(cell_parts["s_via"], name=f"s_via_{row}_{col}", loc=loc,color=Color("gray"))  # Add the shorted via layer
    # Add Cross Align Marker
    marker = make_align_marker(1000,200,20)
    x_offset = 3.1 * spacing_x
    y_offset = 4.5 * spacing_y
    loc = cq.Location(cq.Vector(x_offset, y_offset, 0))
    assy_text.add(marker,name = "AlignMarker", loc = loc, color=Color("gray"))
    # Combine all layers into one final assembly.
    final_assy = cq.Assembly()
    final_assy.add(assy_bot_CI, name="bot_CI_layer")
    final_assy.add(assy_signal_CI, name="signal_CI_layer")
    final_assy.add(assy_via, name="via_layer")
    final_assy.add(assy_top_ci, name="top_electrode_layer")
    final_assy.add(assy_DI, name="DI_layer")
    final_assy.add(assy_s_via, name="s_via_layer")  # Add the shorted via layer if needed
    final_assy.add(assy_text, name="align_marker")
    
    return (assy_bot_CI, assy_signal_CI, assy_via, assy_top_ci, assy_DI, assy_s_via,assy_text, final_assy)

# Runcode
reset_show()
# Build the assemblies.
assy_bot_CI, assy_signal_CI, assy_via, assy_top_ci, assy_DI, assy_s_via,assy_text, final_assy = build_array_test()

# Display the final combined assembly.
show_object(final_assy, name="FinalAssembly")
# Export each individual layer to a STEP file.

ccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccccc


## Export the test file (STEP)

In [27]:
# Define the output folder.
output_folder = "c1-output-test"
os.makedirs(output_folder, exist_ok=True)


# Export the combined final assembly.
final_assy.save(os.path.join(output_folder, "C1-Test.step"))

/Users/ryan/Project/Python-Cad/.conda/lib/python3.11/site-packages/cadquery/utils.py:39: FutureWarning: save will be removed in the next release.
  warn(f"{f.__name__} will be removed in the next release.", FutureWarning)
